In [24]:
import DataManager as manager
import DataPuller as puller
import Predictors as pr
import plotly.express as ex
import plotly.graph_objects as go
import numpy as np


In [27]:
predictor = "RF"
results = manager.load("{}_results".format(predictor))
data = manager.load("2020-07-20-2020-07-28:1d")

high = (data["high"] - data["open"])/data["open"] * 100
low = (data["open"] - data["low"])/data["open"] * 100


fig = ex.scatter(x=results["{}_predicted".format(predictor)][:5970], y=[high[1:], low[1:], data["inter-diff"][1:]], trendline=True)
fig.show()

In [22]:
predictor = "BAYES"
results = manager.load("{}_results".format(predictor))
data = manager.load("2020-07-20-2020-07-28:1d")

high = (data["high"] - data["open"])/data["open"] * 100
low = (data["open"] - data["low"])/data["open"] * 100

fig = ex.scatter(x=results["{}_predicted".format(predictor)][:5970], y=[high[1:], low[1:]])
fig.show()

In [23]:
predictor = "MLP"
results = manager.load("{}_results".format(predictor))
data = manager.load("2020-07-20-2020-07-28:1d")

high = (data["high"] - data["open"])/data["open"] * 100
low = (data["open"] - data["low"])/data["open"] * 100

fig = ex.scatter(x=results["{}_predicted".format(predictor)][:5970], y=[high[1:], low[1:]])
fig.show()

In [2]:
# results = manager.load("MLP_results")
# print(results.shape)


YOAMAMA, 14


In [ ]:
actual = results["MLP_actual"].values
predicted = results["MLP_predicted"].values

predicted_profit_s = np.sum(predicted)
predicted_profit_p = np.prod(predicted)
actual_profit_s = np.sum(actual)
actual_profit_p = np.prod(actual)

signs = np.where(predicted > 0, 1, -1)
predicted_actual = np.abs(actual) * signs

predicted_actual_profit_s = np.sum(predicted_actual)
predicted_actual_profit_p = np.prod(predicted_actual)

print("Pr:Profit:S")
print(predicted_profit_s)

print("Pr:Profit:P")
print(predicted_profit_p)
print("-" * 70)

In [45]:
# data = manager.pull_prepare_save("1997-01-01","2020-08-12", "1d")
data = manager.load("1997-01-01-2020-08-12:1d")
models = []
predictions = []
aes = []
maes = []
stds = []
for i in range(1, 10):
    models.append(pr.mlp_load("MLP_{}".format(i)))
    pre, _, _, _ = pr.evaluate(models[-1], data, all=True)
    _, ae, mae, std = pr.evaluate(models[-1], data, all=False)
    predictions.append(pre)
    aes.append(ae)
    maes.append(mae)
    stds.append(std)

for i in range(9):
    print("MLP - ",i+1)
    print("MAE: ", maes[i])
    print("STD: ", stds[i])



maes = np.asarray(maes)
maes /= np.sum(maes)

psum = np.copy(predictions[0])
ppsum = predictions[0] * maes[0] 

for i in range(1, 9):
    psum += predictions[i]
    ppsum += (predictions[i] * maes[i])

predictions.append(psum / 9)
predictions.append(ppsum) 
# model1 = pr.mlp_load("MLP_1")
# model2 = pr.mlp_load("MLP_2")
# model3 = pr.mlp_load("MLP_3")

# pre1, ma1, std1 = pr.compile_result("MLP_1", model1, data)
# pre2, ma2, std2 = pr.compile_result("MLP_2", model2, data)
# pre3, ma3, std3 = pr.compile_result("MLP_3", model3, data)

# print("Model1: {}, {}, {}".format(pre1, ma1, std1))
# print("Model2: {}, {}, {}".format(pre2, ma2, std2))
# print("Model3: {}, {}, {}".format(pre3, ma3, std3))

MLP -  1
MAE:  0.6640402677122169
STD:  0.6554874664452126
MLP -  2
MAE:  0.2879419910709978
STD:  0.3722377419292205
MLP -  3
MAE:  0.20495387105530452
STD:  0.26440694366815526
MLP -  4
MAE:  0.2138304693865112
STD:  0.28675757931845175
MLP -  5
MAE:  0.1474884716861609
STD:  0.2286728284115804
MLP -  6
MAE:  0.24985757035395215
STD:  0.3044447448324777
MLP -  7
MAE:  0.2608854920472122
STD:  0.3338222055589111
MLP -  8
MAE:  0.3139667482668585
STD:  0.4017179914905017
MLP -  9
MAE:  0.19533091201790034
STD:  0.24660914603576564


In [46]:
high = (data["high"] - data["open"])/data["open"] * 100
low = (data["low"] - data["open"])/data["open"] * 100
actual = data["inter-diff"]

actual = actual[-20:].values
actual = np.append(actual, 0)

high = high[-20:].values
high = np.append(high, 0)

low = low[-20:].values
low = np.append(low, 0)


fig = go.Figure()

fig.add_trace(go.Scatter(
                x=np.arange(21),
                y=actual,
                mode='lines+markers',
                name='Actual',
                marker_color='black'))

fig.add_trace(go.Scatter(
                x=np.arange(21),
                y=high,
                mode='markers',
                name='High',
                marker_color='blue'))
                
fig.add_trace(go.Scatter(
                x=np.arange(21),
                y=low,
                mode='markers',
                name='Low',
                marker_color='red'))

for i in range(11):
    fig.add_trace(go.Scatter(
                x=np.arange(21),
                y=predictions[i],
                mode='lines+markers',
                name='MLP_{}'.format(i),
                marker_color='green'))
                
fig.show()

In [42]:
print(np.asarray(predictions).shape)

(11,)
